# VacationPy
---

## Starter Code to Import Libraries and Load the Weather and Coordinates Data

In [49]:
# Dependencies and Setup
import hvplot.pandas
import pandas as pd
import requests

# Import API key
from api_keys import geoapify_key


In [50]:
# Load the CSV file created in Part 1 into a Pandas DataFrame
city_data_df = pd.read_csv("output_data/cities.csv")

# Display sample data
city_data_df.head()

City_ID          City      Lat       Lng  Max Temp  Humidity  Cloudiness  \
0        0      waitangi -43.9535 -176.5597     14.34        96          89   
1        1        bethel  41.3712  -73.4140      4.05        64          40   
2        2     adamstown -25.0660 -130.1015     23.34        65          79   
3        3  invercargill -46.4000  168.3500     11.68        93          91   
4        4        soller  39.7662    2.7152     17.14        62         100   

   Wind Speed Country        Date  
0        1.34      NZ  1711794322  
1        1.34      US  1711794323  
2       11.22      PN  1711794323  
3        0.89      NZ  1711794204  
4        5.76      ES  1711794323

---

### Step 1: Create a map that displays a point for every city in the `city_data_df` DataFrame. The size of the point should be the humidity in each city.

In [74]:
%%capture --no-display
# Create a map plot with points for each city, where size represents humidity
map_plot = city_data_df.hvplot.points(x='Lng', y='Lat', 
                                      geo=True, 
                                      hover_cols=['City', 'Humidity'], 
                                      tiles='OSM',
                                      size='Humidity',
                                      color='Humidity',
                                      legend='right',
                                      alpha=.5,
                                      label='City',
                                      coastline=True,
                                      colorbar=False,
                                      )

# Display the map plot
map_plot

:Overlay
   .WMTS.I      :WMTS   [Longitude,Latitude]
   .Points.City :Points   [Lng,Lat]   (Humidity,City)
   .Coastline.I :Feature   [Longitude,Latitude]

In [20]:
%%capture --no-display
# Create a map plot with points for each city, where size represents humidity
map_plot = city_data_df.hvplot.scatter(x='Lng', y='Lat', size='Humidity', cmap='rainbow', by='City',
                                       geo=True, hover_cols=['City', 'Humidity'],
                                       legend='right', tiles='CartoLight', xlim=(-180, 180), ylim=(-90, 90))

# Display the map plot
map_plot

:Overlay
   .WMTS.I      :WMTS   [Longitude,Latitude]
   .NdOverlay.I :NdOverlay   [City]
      :Scatter   [Lng]   (Lat,Humidity,City)

In [8]:
%%capture --no-display
# Create a map plot with points for each city, where size represents humidity
map_plot = city_data_df.hvplot.scatter(x='Lng', y='Lat', size='Humidity', cmap='rainbow', by='City',
                                       geo=True,hover_cols=['City', 'Humidity'],
                                       legend='right', fill_alpha=.5)

# Display the map plot
map_plot

:NdOverlay   [City]
   :Scatter   [Lng]   (Lat,Humidity,City)

### Step 2: Narrow down the `city_data_df` DataFrame to find your ideal weather condition

In [52]:
# Narrow down cities that fit criteria and drop any results with null values
temp_filt = (city_data_df['Max Temp']>15) & (city_data_df['Max Temp']<30)
lat_filt = (city_data_df['Lat']>15) & (city_data_df['Lat']<50)
long_filt = (city_data_df['Lng']>-120) & (city_data_df['Lng']<-80)
hum_filt =(city_data_df['Humidity']>10) & (city_data_df['Humidity']<=100)
ideal_weather_df = city_data_df[temp_filt&lat_filt&hum_filt&long_filt]

# Drop any rows with null values
ideal_weather_df.dropna()

# Display sample data
ideal_weather_df


City_ID                    City      Lat       Lng  Max Temp  Humidity  \
83        83               champoton  19.3500  -90.7167     20.25        81   
130      130                   crane  31.3974 -102.3501     16.29        73   
184      184             isla aguada  18.7833  -91.4667     23.11        72   
195      195         lazaro cardenas  17.9583 -102.2000     20.74        62   
203      203                galliano  29.4422  -90.2992     17.00        82   
220      220      brisas de zicatela  15.8369  -97.0419     25.46        71   
234      234                celestun  20.8667  -90.4000     20.47        75   
251      251             sellersburg  38.3981  -85.7550     15.99        48   
253      253         dzilam gonzalez  21.2833  -88.9333     17.00        80   
257      257            san patricio  28.0170  -97.5169     21.02        85   
268      268                 cabanas  22.9758  -82.9219     19.64        71   
277      277          cabo san lucas  22.8909 -109.9124     18.75        91   
330      330                mazatlan  23.2167 -106.4167     18.28        83   
349      349           bahia de kino  28.8333 -111.9333     18.79        81   
434      434                robinson  31.4677  -97.1147     18.14        89   
523      523               ingleside  27.8778  -97.2117     21.10        88   
564      564                  panaba  21.2833  -88.2667     17.05        79   
565      565  tlahualilo de zaragoza  26.1167 -103.4500     18.59        14   

     Cloudiness  Wind Speed Country        Date  
83            1        4.50      MX  1711794338  
130          99        4.80      US  1711794346  
184          91        6.95      MX  1711794354  
195           0        1.52      MX  1711794357  
203           0        1.54      US  1711794359  
220           5        2.14      MX  1711794362  
234           0        5.73      MX  1711794364  
251          98        5.34      US  1711794276  
253           0        2.09      MX  1711794367  
257          14        6.06      US  1711794368  
268           0        3.63      CU  1711794369  
277          12        2.68      MX  1711794371  
330           0        0.45      MX  1711794284  
349         100        4.51      MX  1711794224  
434         100        7.20      US  1711794404  
523          40        5.14      US  1711794419  
564           0        3.09      MX  1711794425  
565          10        3.44      MX  1711794426

### Step 3: Create a new DataFrame called `hotel_df`.

In [53]:
# Use the Pandas copy function to create DataFrame called hotel_df to store the city, country, coordinates, and humidity
columns_to_copy = ['City', 'Country', 'Lat', 'Lng', 'Humidity']
hotel_df = ideal_weather_df[columns_to_copy].copy()

# Add an empty column, "Hotel Name," to the DataFrame so you can store the hotel found using the Geoapify API
hotel_df['Hotel Name'] = ''

# Display sample data
hotel_df

City Country      Lat       Lng  Humidity Hotel Name
83                champoton      MX  19.3500  -90.7167        81           
130                   crane      US  31.3974 -102.3501        73           
184             isla aguada      MX  18.7833  -91.4667        72           
195         lazaro cardenas      MX  17.9583 -102.2000        62           
203                galliano      US  29.4422  -90.2992        82           
220      brisas de zicatela      MX  15.8369  -97.0419        71           
234                celestun      MX  20.8667  -90.4000        75           
251             sellersburg      US  38.3981  -85.7550        48           
253         dzilam gonzalez      MX  21.2833  -88.9333        80           
257            san patricio      US  28.0170  -97.5169        85           
268                 cabanas      CU  22.9758  -82.9219        71           
277          cabo san lucas      MX  22.8909 -109.9124        91           
330                mazatlan      MX  23.2167 -106.4167        83           
349           bahia de kino      MX  28.8333 -111.9333        81           
434                robinson      US  31.4677  -97.1147        89           
523               ingleside      US  27.8778  -97.2117        88           
564                  panaba      MX  21.2833  -88.2667        79           
565  tlahualilo de zaragoza      MX  26.1167 -103.4500        14

### Step 4: For each city, use the Geoapify API to find the first hotel located within 10,000 metres of your coordinates.

In [76]:
# Set parameters to search for a hotel
radius = 10000
limit = 20
params = {
    "categories":"accommodation.hotel",
    "apiKey": geoapify_key,
    "limit":limit,
}

# Print a message to follow up the hotel search
print("Starting hotel search")

# Iterate through the hotel_df DataFrame
for index, row in hotel_df.iterrows():
    # get latitude, longitude from the DataFrame
    lat = row.iloc[2]
    long = row.iloc[3]
    
    # Add filter and bias parameters with the current city's latitude and longitude to the params dictionary
    params["filter"] = f"circle:{long},{lat},{radius}"
    params["bias"] = f"proximity:{long},{lat}"
    
    # Set base URL
    base_url = "https://api.geoapify.com/v2/places"


    # Make and API request using the params dictionaty
    name_address = requests.get(base_url, params=params)
    
    # Convert the API response to JSON format
    name_address = name_address.json()
    
    # Grab the first hotel from the results and store the name in the hotel_df DataFrame
    try:
        hotel_df.loc[index, "Hotel Name"] = name_address["features"][0]["properties"]["name"]
    except (KeyError, IndexError):
        # If no hotel is found, set the hotel name as "No hotel found".
        hotel_df.loc[index, "Hotel Name"] = "No hotel found"
        
    # Log the search results
    print(f"{hotel_df.loc[index, 'City']} - nearest hotel: {hotel_df.loc[index, 'Hotel Name']}")

# Display sample data
hotel_df

Starting hotel search
champoton - nearest hotel: No hotel found
crane - nearest hotel: No hotel found
isla aguada - nearest hotel: No hotel found
lazaro cardenas - nearest hotel: No hotel found
galliano - nearest hotel: No hotel found
brisas de zicatela - nearest hotel: No hotel found
celestun - nearest hotel: No hotel found
sellersburg - nearest hotel: No hotel found
dzilam gonzalez - nearest hotel: No hotel found
san patricio - nearest hotel: No hotel found
cabanas - nearest hotel: No hotel found
cabo san lucas - nearest hotel: No hotel found
mazatlan - nearest hotel: No hotel found
bahia de kino - nearest hotel: No hotel found
robinson - nearest hotel: No hotel found
ingleside - nearest hotel: No hotel found
panaba - nearest hotel: No hotel found
tlahualilo de zaragoza - nearest hotel: No hotel found


City Country      Lat       Lng  Humidity  \
83                champoton      MX  19.3500  -90.7167        81   
130                   crane      US  31.3974 -102.3501        73   
184             isla aguada      MX  18.7833  -91.4667        72   
195         lazaro cardenas      MX  17.9583 -102.2000        62   
203                galliano      US  29.4422  -90.2992        82   
220      brisas de zicatela      MX  15.8369  -97.0419        71   
234                celestun      MX  20.8667  -90.4000        75   
251             sellersburg      US  38.3981  -85.7550        48   
253         dzilam gonzalez      MX  21.2833  -88.9333        80   
257            san patricio      US  28.0170  -97.5169        85   
268                 cabanas      CU  22.9758  -82.9219        71   
277          cabo san lucas      MX  22.8909 -109.9124        91   
330                mazatlan      MX  23.2167 -106.4167        83   
349           bahia de kino      MX  28.8333 -111.9333        81   
434                robinson      US  31.4677  -97.1147        89   
523               ingleside      US  27.8778  -97.2117        88   
564                  panaba      MX  21.2833  -88.2667        79   
565  tlahualilo de zaragoza      MX  26.1167 -103.4500        14   

         Hotel Name  
83   No hotel found  
130  No hotel found  
184  No hotel found  
195  No hotel found  
203  No hotel found  
220  No hotel found  
234  No hotel found  
251  No hotel found  
253  No hotel found  
257  No hotel found  
268  No hotel found  
277  No hotel found  
330  No hotel found  
349  No hotel found  
434  No hotel found  
523  No hotel found  
564  No hotel found  
565  No hotel found

### Step 5: Add the hotel name and the country as additional information in the hover message for each city in the map.

In [75]:
%%capture --no-display
# Create a map plot with points for each city, where size represents humidity
map_plot = hotel_df.hvplot.points(x='Lng', y='Lat', 
                                      geo=True, 
                                      hover_cols=['City', 'Humidity','Hotel Name', 'Country'], 
                                      tiles='OSM',
                                      size='Humidity',
                                      color='Lat',
                                      legend='right',
                                      alpha=.5,
                                      coastline=True,
                                      colorbar=False,
                                      xlim=(-180, 180), ylim=(-60, 70))

# Display the map plot
map_plot

:Overlay
   .WMTS.I      :WMTS   [Longitude,Latitude]
   .Points.I    :Points   [Lng,Lat]   (Humidity,City,Hotel Name,Country)
   .Coastline.I :Feature   [Longitude,Latitude]

In [7]:
%%capture --no-display

# Configure the map plot
map_plot = hotel_df.hvplot.scatter(x='Lng', y='Lat', size='Humidity', cmap='rainbow', by='City',
                                       geo=True,hover_cols=['City', 'Humidity', 'Hotel Name','Country'],
                                       legend='right', fill_alpha=.5)

# Display the map plot
map_plot

:NdOverlay   [City]
   :Scatter   [Lng]   (Lat,Humidity,City,Hotel Name,Country)